In [1]:
from collections import Counter, defaultdict
import math
import numpy as np
import os
import pandas as pd
import re
from scipy.sparse import csr_matrix

In [2]:
def tokenize_string(my_string):
    """ 
    This is used in tokenize function.
    """
    return re.findall('[\w\&]+', my_string.lower())

In [3]:
def tokenize(songs):
    """
    Append a new column to the songs DataFrame with header 'tokens'.
    This will contain a list of strings, one per token, extracted
    from the 'genre' field of each song. Use the tokenize_string method above.
    Note: you may modify the songs parameter directly; no need to make
    a new copy.
    Params:
      songs...The songs DataFrame
    Returns:
      The songs DataFrame, augmented to include a new column called 'tokens'.
    >>> songs = pd.DataFrame([[linkin park, 'Alternative'], [Baby, 'Rock']], columns=['songId', 'genres'])
    >>> songs = tokenize(songs)
    >>> songs['tokens'].tolist()
    [['Alternative', 'rock']]
    """
    tokenlist=[]
    for index,row in songs.iterrows():
        tokenlist.append(row.title)
    songs['tokens']=tokenlist
    return songs

In [4]:
def featurize(songs):
    """
    Append a new column to the songs DataFrame with header 'features'.
    Each row will contain a csr_matrix of shape (1, num_features). Each
    entry in this matrix will contain the tf-idf value of the term, as
    defined in class:
    tfidf(i, d) := tf(i, d) / max_k tf(k, d) * log10(N/df(i))
    where:
    i is a term
    d is a document (song)
    tf(i, d) is the frequency of term i in document d
    max_k tf(k, d) is the maximum frequency of any term in document d
    N is the number of documents (songs)
    df(i) is the number of unique documents containing term i
    Params:
      songs...The songs DataFrame
    Returns:
      A tuple containing:
      - The songs DataFrame, which has been modified to include a column named 'features'.
      - The vocab, a dict from term to int. Make sure the vocab is sorted alphabetically as in a2 (e.g., {'aardvark': 0, 'boy': 1, ...})
    """
    def tf(word,doc):
        return doc.count(word) / Counter(doc).most_common()[0][1]

    def df(word, doclist):
        return sum(1 for d in doclist if word in d)

    def tfidf(word, doc, dfdict, N):
        return tf(word, doc) * math.log10((N/dfdict[word]))

    def getcsrmatrix(tokens,dfdict,N,vocab):
        matrixRow_list = []
        matrixRow_list = np.zeros((1,len(vocab)),dtype='float')
        for t in tokens:
            if t in vocab:
                matrixRow_list[0][vocab[t]] = tfidf(t,tokens,dfdict,N)
        return csr_matrix(matrixRow_list)

    N=len(songs)
    doclist = songs['tokens'].tolist()
    vocab = { s:x for x,s in enumerate(sorted(list(set(s for s in doclist)))) }
    dfdict = {}
    for v in vocab.items():
        dfdict[v[0]] = df(v[0],doclist)

    csrlist = []
    for index, row in songs.iterrows():
         csrlist.append(getcsrmatrix(row['tokens'],dfdict,N,vocab))

    songs['features'] =  csrlist
    return (songs,vocab)

In [5]:
def train_test_split(ratings):
    """
    Returns a random split of the ratings matrix into a training and testing set.
    """
    test = set(range(len(ratings))[::1000])
    train = sorted(set(range(len(ratings))) - test)
    test = sorted(test)
    return ratings.iloc[train], ratings.iloc[test]

In [6]:
def cosine_sim(a, b):
    """
    Compute the cosine similarity between two 1-d csr_matrices.
    Each matrix represents the tf-idf feature vector of a movie.
    Params:
      a...A csr_matrix with shape (1, number_features)
      b...A csr_matrix with shape (1, number_features)
    Returns:
      The cosine similarity, defined as: dot(a, b) / ||a|| * ||b||
      where ||a|| indicates the Euclidean norm (aka L2 norm) of vector a.
    """
    v1 = a.toarray()[0]
    v2  = b.toarray()[0]
    return sum(i[0] * i[1] for i in zip(v1, v2))/(math.sqrt(sum([i*i for i in v1]))*math.sqrt(sum([i*i for i in v2])))

In [7]:
def make_predictions(songs, ratings_train, ratings_test):
    """
    Using the ratings in ratings_train, predict the ratings for each
    row in ratings_test.
    
    Params:
      songs..........The songs DataFrame.
      ratings_train...The subset of ratings used for making predictions. These are the "historical" data.
      ratings_test....The subset of ratings that need to predicted. These are the "future" data.
    Returns:
      A numpy array containing one predicted rating for each element of ratings_test.
    """
    result = []
    for index,row in ratings_test.iterrows():
        mlist = list(ratings_train.loc[ratings_train['user_id'] == row['user_id']]['book_id'])
        csrlist = list(songs.loc[songs['book_id'].isin(mlist)]['features'])
        mrlist = list(ratings_train.loc[ratings_train['user_id'] ==row['user_id']]['rating'])
        cmlist = [cosine_sim(c,songs.loc[songs['book_id'] ==row['book_id']]['features'].values[0]) for c in csrlist]
        wan = sum([ v*mrlist[i] for i,v in enumerate(cmlist) if v>0 ])
        wadlist = [i for i in cmlist if i>0]
        if (len(wadlist)>0):
            result.append(wan/sum(wadlist))
        else:
            result.append(np.mean(mrlist))
    return np.array(result)

In [8]:
def mean_absolute_error(predictions, ratings_test):
    """
    Return the mean absolute error of the predictions.
    """
    return np.abs(predictions - np.array(ratings_test.rating)).mean()

In [10]:
books = pd.read_csv("../data/books.csv")
book_tags = pd.read_csv("../data/book_tags.csv")
tags = pd.read_csv("../data/tags.csv")
ratings = pd.read_csv("../data/ratings.csv")

In [11]:
pd.set_option("display.max_rows", None)

In [12]:
pd.DataFrame(np.unique(tags['tag_name']))

0
0                                        -
1                                     --1-
2                                    --10-
3                                    --12-
4                                   --122-
5                                   --166-
6                                    --17-
7                                    --19-
8                                     --2-
9                                   --258-
10                                    --3-
11                                   --33-
12                                    --4-
13                                    --5-
14                                   --51-
15                                    --6-
16                                   --62-
17                                    --8-
18                                   --99-
19             --available-at-raspberrys--
20                                 -2001--
21                                -calif--
22                                  -d-c--
23                                   -dean
24                               -england-
25                                -fiction
26                              -fictional
27                             -fictitious
28                              -football-
29                                 -george
30                                    -gr-
31                                -history
32                              -imaginary
33                                 -italy-
34                                   -la--
35                                    -los
36                                 -mass--
37                                -murder-
38                                  -n-y--
39                            -non-poetry-
40                             -performing
41                                   -post
42                            -psychology-
43                                   -read
44                                 -single
45                               -specific
46                             -television
47                                       0
48                        0-0-0-0cant-find
49                               0-0-bingo
50                         0-4-star-rating
51                 0-a-find-2016-summer-00
52                                  0-all2
53                  0-best-picture-younger
54                                 0-boxed
55                                     0-c
56                          0-eric-s-books
57                            0-house-lbkc
58                                0-kindle
59                            0-love-funny
60                  0-made-me-cry-moved-me
61                            0-nonfiction
62                                 0-owned
63                             0-paperback
64                        0-pgs-200-to-299
65                          0-physical-own
66                                 0-plays
67                                   0-plc
68                           0-tbr-axz-usa
69                          00-exploring-1
70                  00-graphic-novels-read
71                             00-in-class
72                           00-to-read-00
73                           00-to-read-02
74                                    0000
75                             0000-to-buy
76                                   00000
77                        0000_notverified
78                     000src-su-25-11-3-x
79                000src-w-15-01-i-me-mine
80                           001-150-pages
81                               001-ebook
82                       002-read-cookbook
83                 002-une-bonne-selection
84                                     007
85                            008-strategy
86                                      01
87                     01-alphabet-authors
88                            01-distopias
89                           01-ecookbooks
90                             01-folklore
91                 01-irl-bookshelf-comics
92                                 01-mine

In [13]:
books.head()

id  book_id  best_book_id  work_id  books_count       isbn        isbn13  \
0   1  2767052       2767052  2792775          272  439023483  9.780439e+12   
1   2        3             3  4640799          491  439554934  9.780440e+12   
2   3    41865         41865  3212258          226  316015849  9.780316e+12   
3   4     2657          2657  3275794          487   61120081  9.780061e+12   
4   5     4671          4671   245494         1356  743273567  9.780743e+12   

                       authors  original_publication_year  \
0              Suzanne Collins                     2008.0   
1  J.K. Rowling, Mary GrandPré                     1997.0   
2              Stephenie Meyer                     2005.0   
3                   Harper Lee                     1960.0   
4          F. Scott Fitzgerald                     1925.0   

                             original_title  ... ratings_count  \
0                          The Hunger Games  ...       4780653   
1  Harry Potter and the Philosopher's Stone  ...       4602479   
2                                  Twilight  ...       3866839   
3                     To Kill a Mockingbird  ...       3198671   
4                          The Great Gatsby  ...       2683664   

  work_ratings_count  work_text_reviews_count  ratings_1  ratings_2  \
0            4942365                   155254      66715     127936   
1            4800065                    75867      75504     101676   
2            3916824                    95009     456191     436802   
3            3340896                    72586      60427     117415   
4            2773745                    51992      86236     197621   

   ratings_3  ratings_4  ratings_5  \
0     560092    1481305    2706317   
1     455024    1156318    3011543   
2     793319     875073    1355439   
3     446835    1001952    1714267   
4     606158     936012     947718   

                                           image_url  \
0  https://images.gr-assets.com/books/1447303603m...   
1  https://images.gr-assets.com/books/1474154022m...   
2  https://images.gr-assets.com/books/1361039443m...   
3  https://images.gr-assets.com/books/1361975680m...   
4  https://images.gr-assets.com/books/1490528560m...   

                                     small_image_url  
0  https://images.gr-assets.com/books/1447303603s...  
1  https://images.gr-assets.com/books/1474154022s...  
2  https://images.gr-assets.com/books/1361039443s...  
3  https://images.gr-assets.com/books/1361975680s...  
4  https://images.gr-assets.com/books/1490528560s...  

[5 rows x 23 columns]

In [14]:
ratings.head()

book_id  user_id  rating
0        1      314       5
1        1      439       3
2        1      588       5
3        1     1169       4
4        1     1185       4

In [15]:
books = books[['book_id','title','authors']]

In [16]:
books.head()

book_id                                              title  \
0  2767052            The Hunger Games (The Hunger Games, #1)   
1        3  Harry Potter and the Sorcerer's Stone (Harry P...   
2    41865                            Twilight (Twilight, #1)   
3     2657                              To Kill a Mockingbird   
4     4671                                   The Great Gatsby   

                       authors  
0              Suzanne Collins  
1  J.K. Rowling, Mary GrandPré  
2              Stephenie Meyer  
3                   Harper Lee  
4          F. Scott Fitzgerald

In [17]:
books = books.drop_duplicates(['book_id'])

In [18]:
books.shape

(10000, 3)

In [ ]:
books = tokenize(books)
books.head()

In [ ]:
books, vocab = featurize(books)

In [ ]:
books.head()

In [ ]:
vocab

In [ ]:
print('Favorites:')
print(sorted(vocab.items())[:100])

In [ ]:
ratings_train, ratings_test = train_test_split(ratings)

In [ ]:
print('%d training ratings; %d testing ratings' % (len(ratings_train), len(ratings_test)))
predictions = make_predictions(books, ratings_train, ratings_test)
print('error=%f' % mean_absolute_error(predictions, ratings_test))
print(predictions[:100])